In [20]:
import sys
import os
from os import sep
from os.path import dirname, realpath, splitext
from pathlib import Path
from functools import partial
from itertools import product
import logging

def get_cwd(fname, subdir, crunch_dir=realpath(Path.home()) +sep +'crunch' +sep):
    """
    Convenience function to make a directory string for the current file based on inputs.
    Jupyter Notebook in Anaconda invokes the Python interpreter in Anaconda's subdirectory
    which sis why changing sys.argv[0] is necessary. In the future a better way to do this
    should be preferred..
    """
    return crunch_dir +subdir +fname

def fix_path(cwd):
    """
    Convenience function to fix argv and python path so that jupyter notebook can run the same as
    any script in crunch.
    """
    sys.argv[0] = cwd
    module_path = os.path.abspath(os.path.join('..'))
    if module_path not in sys.path:
        sys.path.append(module_path)

fix_path(get_cwd('inspect_raw.ipynb', 'raw' +sep))

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from dask import delayed, compute
from numba import jit, vectorize, float64, uint
from sortedcontainers import SortedList, SortedSet 

from ipywidgets import interact, interactive, fixed
from IPython.display import display

pd.set_option('display.max_rows', 500)
# pd.set_option('display.height', 500)
pd.set_option('display.max_columns', 50)

from common_util import DT_HOURLY_FREQ, DT_CAL_DAILY_FREQ, DT_BIZ_DAILY_FREQ, list_get_dict, inner_join, right_join, get_custom_biz_freq_df, query_df, search_df, chained_filter, recursive_dict, benchmark
from common_util import RECON_DIR, load_df, dump_df, load_json, df_count, df_value_count, outer_join, left_join, getcon, string_df_join_to_ser, is_df, is_ser, count_nn_nz_df, pairwise, cust_count, get_pardir_from_path
from raw.common import default_pathsfile
from data.data_api import DataAPI
from data.access_util import df_getters as dg, col_subsetters2 as cs2

Manually change csv and overwrite parquet

In [18]:
for path, dirs, files in os.walk('trmi', topdown=False):
    if (len(files)==0): continue
 #   print(files)
    for fcsv in filter(lambda fname: fname.endswith('.csv'), files):
        new = load_df(fcsv, dir_path=path, data_format='csv')
        dump_df(new, fcsv[:-len('.csv')], dir_path=path)

In [19]:
for path, dirs, files in os.walk('trmi', topdown=False):
    if (len(files)==0): continue
 #   print(files)
    for fcsv in filter(lambda fname: fname.endswith('.parquet'), files):
        new = load_df(fcsv, dir_path=path)
        print(new)

/home/kev/miniconda3/lib/python3.6/site-packages/pyarrow/pandas_compat.py:698: FutureWarning: .labels was deprecated in version 0.24.0. Use .codes instead.
  labels = getattr(columns, 'labels', None) or [
/home/kev/miniconda3/lib/python3.6/site-packages/pyarrow/pandas_compat.py:725: FutureWarning: the 'labels' keyword is deprecated, use 'codes' instead
  return pd.MultiIndex(levels=new_levels, labels=labels, names=columns.names)
/home/kev/miniconda3/lib/python3.6/site-packages/pyarrow/pandas_compat.py:742: FutureWarning: .labels was deprecated in version 0.24.0. Use .codes instead.
  labels, = index.labels


                 etf2_ver   etf2_buzz_N  etf2_relativeBuzz_N  \
id                                                             
1998-01-01 18:00    2.2.0     77.000000             0.011721   
1998-01-01 19:00    2.2.0     77.000000             0.011721   
1998-01-01 20:00    2.2.0     77.000000             0.011721   
1998-01-01 21:00    2.2.0     77.000000             0.011721   
1998-01-01 22:00    2.2.0     77.000000             0.011721   
1998-01-01 23:00    2.2.0     77.000000             0.011721   
1998-01-02 00:00    2.2.0     77.000000             0.011721   
1998-01-02 01:00    2.2.0     77.000000             0.011364   
1998-01-02 02:00    2.2.0     77.000000             0.011364   
1998-01-02 03:00    2.2.0     77.000000             0.011364   
1998-01-02 04:00    2.2.0     77.000000             0.011364   
1998-01-02 05:00    2.2.0     77.000000             0.011364   
1998-01-02 06:00    2.2.0     77.000000             0.011364   
1998-01-02 07:00    2.2.0     77.000000 

                 etf2_ver    etf2_buzz_N  etf2_relativeBuzz_N  \
id                                                              
1998-01-01 18:00    2.2.0    2134.900000             0.324967   
1998-01-01 19:00    2.2.0    2134.900000             0.324967   
1998-01-01 20:00    2.2.0    2134.900000             0.324967   
1998-01-01 21:00    2.2.0    2134.900000             0.324967   
1998-01-01 22:00    2.2.0    2134.900000             0.324967   
1998-01-01 23:00    2.2.0    2134.900000             0.324967   
1998-01-02 00:00    2.2.0    2134.900000             0.324967   
1998-01-02 01:00    2.2.0    2136.900000             0.315368   
1998-01-02 02:00    2.2.0    2136.900000             0.315368   
1998-01-02 03:00    2.2.0    2136.900000             0.315368   
1998-01-02 04:00    2.2.0    2136.900000             0.315368   
1998-01-02 05:00    2.2.0    2136.900000             0.315368   
1998-01-02 06:00    2.2.0    2136.900000             0.315368   
1998-01-02 07:00    2.2.0

                 etf2_ver   etf2_buzz_N  etf2_relativeBuzz_N  \
id                                                             
1998-01-01 18:00    2.2.0     46.000000             0.007002   
1998-01-01 19:00    2.2.0     46.000000             0.007002   
1998-01-01 20:00    2.2.0     46.000000             0.007002   
1998-01-01 21:00    2.2.0     46.000000             0.007002   
1998-01-01 22:00    2.2.0     46.000000             0.007002   
1998-01-01 23:00    2.2.0     46.000000             0.007002   
1998-01-02 00:00    2.2.0     46.000000             0.007002   
1998-01-02 01:00    2.2.0     46.000000             0.006789   
1998-01-02 02:00    2.2.0     46.000000             0.006789   
1998-01-02 03:00    2.2.0     46.000000             0.006789   
1998-01-02 04:00    2.2.0     46.000000             0.006789   
1998-01-02 05:00    2.2.0     46.000000             0.006789   
1998-01-02 06:00    2.2.0     46.000000             0.006789   
1998-01-02 07:00    2.2.0     46.000000 

                 etf2_ver   etf2_buzz_N  etf2_relativeBuzz_N  \
id                                                             
1998-01-01 18:00    2.2.0     88.000000             0.013395   
1998-01-01 19:00    2.2.0     88.000000             0.013395   
1998-01-01 20:00    2.2.0     88.000000             0.013395   
1998-01-01 21:00    2.2.0     88.000000             0.013395   
1998-01-01 22:00    2.2.0     88.000000             0.013395   
1998-01-01 23:00    2.2.0     88.000000             0.013395   
1998-01-02 00:00    2.2.0     88.000000             0.013395   
1998-01-02 01:00    2.2.0     88.000000             0.012987   
1998-01-02 02:00    2.2.0     88.000000             0.012987   
1998-01-02 03:00    2.2.0     88.000000             0.012987   
1998-01-02 04:00    2.2.0     88.000000             0.012987   
1998-01-02 05:00    2.2.0     88.000000             0.012987   
1998-01-02 06:00    2.2.0     88.000000             0.012987   
1998-01-02 07:00    2.2.0     88.000000 

...

                 etf3_ver    etf3_buzz_N  etf3_sentiment_N  etf3_optimism_N  \
id                                                                            
1998-01-01 01:00    3.0.9    6489.400000         -0.044765        -0.002003   
1998-01-01 02:00    3.0.9    6458.400000         -0.048696        -0.002013   
1998-01-01 03:00    3.0.9    6458.400000         -0.048696        -0.002013   
1998-01-01 04:00    3.0.9    6458.400000         -0.048696        -0.002013   
1998-01-01 05:00    3.0.9    6431.400000         -0.047657        -0.001244   
1998-01-01 06:00    3.0.9    6431.400000         -0.047657        -0.001244   
1998-01-01 07:00    3.0.9    6431.400000         -0.047657        -0.001244   
1998-01-01 08:00    3.0.9    6430.400000         -0.047664        -0.001244   
1998-01-01 09:00    3.0.9    6407.400000         -0.047211        -0.001249   
1998-01-01 10:00    3.0.9    6402.300000         -0.047405        -0.001406   
1998-01-01 11:00    3.0.9    6402.300000         -0.

                 etf3_ver   etf3_buzz_N  etf3_sentiment_N  etf3_optimism_N  \
id                                                                           
1998-01-01 01:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 02:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 03:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 04:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 05:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 06:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 07:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 08:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 09:00    3.0.9    478.500000         -0.063741        -0.034483   
1998-01-01 10:00    3.0.9    474.400000         -0.066400        -0.036889   
1998-01-01 11:00    3.0.9    474.400000         -0.066400       

                 etf3_ver    etf3_buzz_N  etf3_sentiment_N  etf3_optimism_N  \
id                                                                            
1998-01-01 01:00    3.0.9     543.900000          0.015628        -0.014709   
1998-01-01 02:00    3.0.9     512.900000         -0.030220        -0.015598   
1998-01-01 03:00    3.0.9     512.900000         -0.030220        -0.015598   
1998-01-01 04:00    3.0.9     512.900000         -0.030220        -0.015598   
1998-01-01 05:00    3.0.9     495.900000         -0.027223        -0.016132   
1998-01-01 06:00    3.0.9     495.900000         -0.027223        -0.016132   
1998-01-01 07:00    3.0.9     495.900000         -0.027223        -0.016132   
1998-01-01 08:00    3.0.9     495.900000         -0.027223        -0.016132   
1998-01-01 09:00    3.0.9     472.900000         -0.020089        -0.016917   
1998-01-01 10:00    3.0.9     472.900000         -0.020089        -0.016917   
1998-01-01 11:00    3.0.9     472.900000         -0.

                 enm3_ver   enm3_buzz_N  enm3_sentiment_N  enm3_optimism_N  \
id                                                                           
1998-01-01 01:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 02:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 03:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 04:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 05:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 06:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 07:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 08:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 09:00    3.0.9     80.000000          0.225000         0.162500   
1998-01-01 10:00    3.0.9     79.000000          0.240506         0.164557   
1998-01-01 11:00    3.0.9     79.000000          0.240506       

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

